#1. Create a table, load data, and query data

In [ ]:

CREATE TABLE C_amazon_categories(
  id BIGINT NOT NULL PRIMARY KEY,
  category_name STRING NOT NULL,
  category_type STRING NOT NULL
) USING DELTA;

In [ ]:
INSERT INTO P_amazon_products 
SELECT 
    CAST(asin AS STRING) AS asin,
    CAST(title AS STRING) AS title,
    CAST(imgUrl AS STRING) AS imgUrl,
    CAST(productURL AS STRING) AS productURL,
    CAST(stars AS DECIMAL(3,2)) AS stars,
    CAST(reviews AS BIGINT) AS reviews,
    CAST(price AS DECIMAL(10,2)) AS price,
    CAST(listPrice AS DECIMAL(10,2)) AS listPrice,
    CAST(category_id AS INT) AS category_id,
    CAST(isBestSeller AS BOOLEAN) AS isBestSelling,
    CAST(boughtInLastMonth AS BIGINT) AS boughtInlastMonth
FROM amazon_products_ss;

num_affected_rows num_inserted_rows 1426337 1426337

In [ ]:
%sql
-- Load data into one place with schema definitions
show tables;

database tableName isTemporary default amazon_categories false default amazon_categories_raw false default amazon_categories_raww false default amazon_categories_with_type false default amazon_products false default amazon_products_raww false default c_amazon_categories false default p_amazon_products false _sqldf true

In [ ]:
DESCRIBE amazon_categories_with_type;

col_name data_type comment id bigint null category_name string null category_type string null

# Transform and load raw data

In [ ]:
INSERT INTO C_amazon_categories 
SELECT 
    CAST(id AS INT) AS id,
    CAST(category_name AS STRING) AS category_name,
    CAST(category_type AS STRING) AS category_type
FROM amazon_categories_with_type;

num_affected_rows num_inserted_rows 248 248

In [ ]:
-- Check schema
DESCRIBE amazon_products_ss;

col_name data_type comment asin string null title string null imgUrl string null productURL string null stars double null reviews int null price double null listPrice double null category_id int null isBestSeller boolean null boughtInLastMonth int null

# Raw data validation

In [ ]:
SELECT COUNT(*) FROM P_amazon_products;

COUNT(*) 1426337

In [ ]:
-- 1. Check the basic number
SELECT COUNT(*) FROM P_amazon_products;

-- 2.NULL 값 체크
SELECT 
    COUNT(*) as total_rows,
    COUNT(asin) as non_null_asin,
    COUNT(title) as non_null_title,
    COUNT(price) as non_null_price
FROM P_amazon_products;

-- 3.Check sample data
SELECT * FROM P_amazon_products LIMIT 5;

asin title imgUrl productURL stars reviews price listPrice category_id isBestSelling boughtInlastMonth B08P86PDLZ 39 x 138 Inch Cellophane Wrap Paper, 2.3 Mil Thick Cellophane Paper with 6 Rolls Colorful Wrap Ribbon for Christmas Holiday DIY Present Wrapping or Basket Filling (Blue) https://m.media-amazon.com/images/I/715blmlfUEL._AC_UL320_.jpg https://www.amazon.com/dp/B08P86PDLZ 3.60 0 6.99 0.00 12 false 0 B0CC2DX6RN 100 Pcs Funeral Ribbons Memorial Ribbon Funeral Pins Classic Memorial Service Respect Meditation Personalized Ribbon Bow with Safety Pins for Mourning Remembrance Day Funeral Event (Red) https://m.media-amazon.com/images/I/91jxLdTRxAL._AC_UL320_.jpg https://www.amazon.com/dp/B0CC2DX6RN 1.00 0 16.99 19.99 12 false 0 B01NBK18HN Burlap Ribbon Perfect for Wedding Home Decoration Gift Wrap Bows Made Handmade Art Crafts 1-1/2 Inch X 10 Yard Spool (Royal Blue) https://m.media-amazon.com/images/I/71VKLAS9wVL._AC_UL320_.jpg https://www.amazon.com/dp/B01NBK18HN 4.70 0 8.99 0.00 12 false 0 B07TH9B2ZR APQ Clear Gusseted Poly Bags 5 x 3 x 15 Inch. Pack of 100 Plastic Bread Bags. 2 Mil Thick Open Top Clear Plastic Bags for Packaging. Waterproof Clear Treat Bags for Bread, Cookies, Candies https://m.media-amazon.com/images/I/71v4dNJi4ZL._AC_UL320_.jpg https://www.amazon.com/dp/B07TH9B2ZR 4.50 0 21.11 0.00 12 false 0 B09X6NVY6H Cutcatwing 4 OZ Navy Blue Crinkle Cut Paper Shred Filler Easter Grass Shredded Raffia Tissue Craft Bedding Cushion Recycled for Small Bag Packing and Filling Gift Baskets Decor https://m.media-amazon.com/images/I/61HKK49RafL._AC_UL320_.jpg https://www.amazon.com/dp/B09X6NVY6H 4.60 0 9.99 0.00 12 false 0

### 1. Check out best sellers by product

In [ ]:
select
  p.asin,
  p.title,
  p.isBestSelling,
  p.category_id,
  c.category_name,
  c.category_type
from p_amazon_products p
inner join c_amazon_categories c on p.category_id = c.id -- After matching the product and category, based on the products that exist on both sides
order by p.asin; -- using aggregate functions
  

asin title isBestSelling category_id category_name category_type 0007268149 Collins Bird Guide: The Most Complete Guide to the Birds of Britain and Europe false 178 Pet Bird Supplies Pet_Supplies 0008288194 The Creativity Code false 263 PC Games & Accessories Gaming 0008537909 The Silmarillion: false 79 Camera & Photo Others 0021402442 Carpentry & Building Construction, Student Edition, 2016 false 138 Commercial Door Products Others 0060219602 Hurray for Hattie Rabbit: Story and pictures (An Early I can read book) false 74 eBook Readers & Accessories Others 0060501960 Presidents' Day false 263 PC Games & Accessories Gaming 0061128392 Biscuit's Pet & Play Easter: A Touch & Feel Book: An Easter And Springtime Book For Kids false 180 Dog Supplies Others 0061132187 One Big Damn Puzzler false 74 eBook Readers & Accessories Others 0061876879 Born Under a Lucky Moon false 74 eBook Readers & Accessories Others 0061953385 Extra Yarn: A Caldecott Honor Award Winner false 3 Knitting & Crochet Supplies Crafts_Sewing 0062665782 A Thousand Heartbeats false 74 eBook Readers & Accessories Others 0062970704 Strange Planet (Strange Planet Series) false 76 Accessories & Supplies Others 006304904X Winning Fixes Everything: How Baseball's Brightest Minds Created Sports' Biggest Mess false 263 PC Games & Accessories Gaming 0063227932 Why Has Nobody Told Me This Before? false 263 PC Games & Accessories Gaming 0072823275 Analyzing The Curriculum false 155 Science Education Supplies Others 0072826843 Evolution of the Earth false 263 PC Games & Accessories Gaming 0091912407 Girl with a One-Track Mind: Confessions of the Seductress Next Door false 74 eBook Readers & Accessories Others 0099557037 Mist over Pendle false 74 eBook Readers & Accessories Others 013369173X Realidades 2 false 74 eBook Readers & Accessories Others 0135031745 Technical Communication in the Twenty-First Century (2nd Edition) false 74 eBook Readers & Accessories Others 0135688302 Diesel Calfskin Genuine Leather Lychee Pattern Watch Band Strap, Buckle Outdoor Sports Watch Bands Suitable for Men's Diesel Watches false 113 Men's Watches Mens_Fashion 0136109802 The Needlepoint Book (The Creative Handcrafts Series) false 8 Needlework Supplies Crafts_Sewing 0140194614 Myths to Live By false 74 eBook Readers & Accessories Others 0140455116 The Republic (Penguin Classics) false 149 Electronic Components Others 0140543635 Un Dia de Nieve (Spanish Edition) false 82 Home Audio & Theater Products Home_Living 0143130722 Ikigai: The Japanese Secret to a Long and Happy Life true 255 Video Games Gaming 0152047379 The Borrowers (Borrowers, 1) false 207 Power Tools & Hand Tools Tools_Hardware 0152049495 Dogzilla false 255 Video Games Gaming 0156031191 Winter's Tale false 263 PC Games & Accessories Gaming 0205062040 CAMO Marksman Pro-X1, Deck Tool for Edge Fastening Installation, 1/16" Spacing, Fits 5-1/4-5-3/4" Wood Decking (0345002) false 212 Building Supplies Others 0205223311 Writing: A Guide for College and Beyond (3rd Edition) false 74 eBook Readers & Accessories Others 0207488770 classic backpack, anti splashing, casual daily travel, laptop backpack false 109 Laptop Bags Electronics 0241971829 One Hundred Years of Solitude false 99 Travel Duffel Bags Travel_Bags 0307449440 Socks from the Toe Up: Essential Techniques and Patterns from Wendy Knits false 3 Knitting & Crochet Supplies Crafts_Sewing 0307743691 Girls in White Dresses false 91 Girls' Clothing Baby_Kids 0307931528 Big Girl Panties false 91 Girls' Clothing Baby_Kids 0307965570 Knitting Pattern Essentials: Adapting and Drafting Knitting Patterns for Great Knitwear false 3 Knitting & Crochet Supplies Crafts_Sewing 0310352061 The Chicken Runs at Midnight: A Daughter’s Message from Heaven That Changed a Father’s Heart and Won a World Series false 263 PC Games & Accessories Gaming 0310742439 Faithgirlz Messenger Bag Pink Medium false 100 Messenger Bags Others 0310822246 Faithgirlz Messenger Bag Grape Med: Medium Fits Most Standard Size Book

In [ ]:
select
  category_type,
  count(*) as total_products,
  sum(case when isBestSelling = true then 1 else 0 end) as --How many best sellers are there in the category?
  best_selling_products,
  round(sum(case when isBestSelling = true then 1 else 0 end) * 100.0 / count(*),2)
  as best_selling_ration -- bestseller and ratio
  from (
    select
      p.asin,
      p.title,
      p.isBestSelling,
      p.category_id,
      c.category_name,
      c.category_type
    from p_amazon_products p
    inner join c_amazon_categories c on p.category_id = c.id -- After matching the/ both table information

  )products_with_category
  group by category_type
  order by total_products desc;

  



category_type total_products best_selling_products best_selling_ration Others 511846 2652 0.52 Baby_Kids 179801 700 0.39 Mens_Fashion 141074 503 0.36 Gaming 82611 411 0.50 Electronics 77070 224 0.29 Automotive 62032 816 1.32 Home_Living 56697 1020 1.80 Jewelry_Accessories 54633 115 0.21 Toys_Games 44778 71 0.16 Crafts_Sewing 42375 126 0.30 Industrial_Science 30721 467 1.52 Arts_Crafts 29324 103 0.35 Sports_Outdoors 24515 898 3.66 Travel_Bags 23693 22 0.09 Tools_Hardware 18741 179 0.96 Health_Beauty 17736 166 0.94 Party_Gifts 15546 22 0.14 Pet_Supplies 13144 25 0.19

> ### first look at the price range distribution by category_type.

In [ ]:
select
  c.category_type,
  case 
     when p.price = 0 then  'free(0)'
     when p.price <= 20 then '0.01~20'
     when p.price <= 50 then '20~50'
     when p.price <= 100 then '50~100'
     when p.price <= 200 then '100~200'
    else '200+'
  end as price_range,
  count(*) as products_count,
  round(count(*) * 100.0 / sum(count(*)) over(partition by c.category_type),2)
from p_amazon_products p
join c_amazon_categories c on p.category_id = c.id
where p.price is not null and p.price >= 0
group by c.category_type,
 case  
     when p.price = 0 then  'free(0)'
     when p.price <= 20 then '0.01~20'
     when p.price <= 50 then '20~50'
     when p.price <= 100 then '50~100'
     when p.price <= 200 then '100~200'
    else '200+'
  end
order by c.category_type, price_range;

category_type price_range products_count round(count(*)*100.0/sum(count(*))OVER(PARTITIONBYc.category_type),2) Arts_Crafts 0.01~20 21758 74.20 Arts_Crafts 100~200 688 2.35 Arts_Crafts 200+ 518 1.77 Arts_Crafts 20~50 4975 16.97 Arts_Crafts 50~100 888 3.03 Arts_Crafts free(0) 497 1.69 Automotive 0.01~20 30586 49.31 Automotive 100~200 4049 6.53 Automotive 200+ 2166 3.49 Automotive 20~50 17730 28.58 Automotive 50~100 7136 11.50 Automotive free(0) 365 0.59 Baby_Kids 0.01~20 91350 50.81 Baby_Kids 100~200 3911 2.18 Baby_Kids 200+ 1449 0.81 Baby_Kids 20~50 66849 37.18 Baby_Kids 50~100 11766 6.54 Baby_Kids free(0) 4476 2.49 Crafts_Sewing 0.01~20 31480 74.29 Crafts_Sewing 100~200 335 0.79 Crafts_Sewing 200+ 132 0.31 Crafts_Sewing 20~50 8275 19.53 Crafts_Sewing 50~100 939 2.22 Crafts_Sewing free(0) 1214 2.86 Electronics 0.01~20 22611 29.34 Electronics 100~200 8513 11.05 Electronics 200+ 12764 16.56 Electronics 20~50 20631 26.77 Electronics 50~100 10382 13.47 Electronics free(0) 2169 2.81 Gaming 0.01~20 32625 39.49 Gaming 100~200 2319 2.81 Gaming 200+ 1091 1.32 Gaming 20~50 31429 38.04 Gaming 50~100 7087 8.58 Gaming free(0) 8060 9.76 Health_Beauty 0.01~20 12829 72.33 Health_Beauty 100~200 181 1.02 Health_Beauty 200+ 34 0.19 Health_Beauty 20~50 3860 21.76 Health_Beauty 50~100 603 3.40 Health_Beauty free(0) 229 1.29 Home_Living 0.01~20 27492 48.49 Home_Living 100~200 2978 5.25 Home_Living 200+ 1981 3.49 Home_Living 20~50 18484 32.60 Home_Living 50~100 4915 8.67 Home_Living free(0) 847 1.49 Industrial_Science 0.01~20 20248 65.91 Industrial_Science 100~200 679 2.21 Industrial_Science 200+ 301 0.98 Industrial_Science 20~50 7230 23.53 Industrial_Science 50~100 1709 5.56 Industrial_Science free(0) 554 1.80 Jewelry_Accessories 0.01~20 41527 76.01 Jewelry_Accessories 100~200 962 1.76 Jewelry_Accessories 200+ 547 1.00 Jewelry_Accessories 20~50 9350 17.11 Jewelry_Accessories 50~100 2055 3.76 Jewelry_Accessories free(0) 192 0.35 Mens_Fashion 0.01~20 32537 23.06 Mens_Fashion 100~200 18474 13.10 Mens_Fashion 200+ 5851 4.15 Mens_Fashion 20~50 55186 39.12 Mens_Fashion 50~100 25824 18.31 Mens_Fashion free(0) 3202 2.27 Others 0.01~20 278665 54.44 Others 100~200 20388 3.98 Others 200+ 11588 2.26 Others 20~50 149805 29.27 Others 50~100 42673 8.34 Others free(0) 8727 1.71 Party_Gifts 0.01~20 13543 87.12 Party_Gifts 100~200 14 0.09 Party_Gifts 200+ 2 0.01 Party_Gifts 20~50 1901 12.23 Party_Gifts 50~100 62 0.40 Party_Gifts free(0) 24 0.15 Pet_Supplies 0.01~20 9075 69.04 Pet_Supplies 100~200 185 1.41 Pet_Supplies 200+ 72 0.55 Pet_Supplies 20~50 2844 21.64 Pet_Supplies 50~100 696 5.30 Pet_Supplies free(0) 272 2.07 Sports_Outdoors 0.01~20 11525 47.01 Sports_Outdoors 100~200 550 2.24 Sports_Outdoors 200+ 139 0.57 Sports_Outdoors 20~50 9902 40.39 Sports_Outdoors 50~100 2121 8.65 Sports_Outdoors free(0) 278 1.13 Tools_Hardware 0.01~20 9991 53.31 Tools_Hardware 100~200 837 4.47 Tools_Hardware 200+ 330 1.76 Tools_Hardware 20~50 5614 29.96 Tools_Hardware 50~100 1664 8.88 Tools_Hardware free(0) 305 1.63 Toys_Games 0.01~20 24842 55.48 Toys_Games 100~200 762 1.70 Toys_Games 200+ 288 0.64 Toys_Games 20~50 15163 33.86 Toys_Games 50~100 2519 5.63 Toys_Games free(0) 1204 2.69 Travel_Bags 0.01~20 14594 61.60 Travel_Bags 100~200 1388 5.86 Travel_Bags 200+ 715 3.02 Travel_Bags 20~50 5289 22.32 Travel_Bags 50~100 1550 6.54 Travel_Bags free(0) 157 0.66

### category_type standard deviation

In [ ]:
select
  c.category_type,
  count(*) as total_products,
  round(avg(p.price),2) as avg_price,
  round(stddev(p.price),2) as std_deviation,
  min(p.price) as min_price,
  max(p.price) as max_price,
  round((stddev(p.price)/avg(p.price))*100,2) as coefficient_of_variation,
  round(max(p.price) - min(p.price), 2) as price_range
from p_amazon_products p
join c_amazon_categories c on p.category_id = c.id
where p.price is not null and p.price >= 0
group by c.category_type
order by std_deviation desc;


category_type total_products avg_price std_deviation min_price max_price coefficient_of_variation price_range Electronics 77070 147.24 360.18 0.00 16468.70 244.62 16468.70 Others 511846 39.46 127.03 0.00 19731.81 321.95 19731.81 Home_Living 56697 46.05 112.46 0.00 5498.81 244.23 5498.81 Arts_Crafts 29324 27.81 107.06 0.00 7599.00 385.03 7599.00 Gaming 82611 33.94 104.13 0.00 10010.00 306.8 10010.00 Crafts_Sewing 42375 18.54 101.39 0.00 19400.00 547.0 19400.00 Mens_Fashion 141074 62.85 88.23 0.00 5750.00 140.38 5750.00 Travel_Bags 23693 40.17 85.28 0.00 2909.55 212.32 2909.55 Automotive 62032 44.98 78.57 0.00 4778.00 174.68 4778.00 Tools_Hardware 18741 34.97 66.62 0.00 3487.99 190.49 3487.99 Toys_Games 44778 26.61 57.43 0.00 7311.46 215.78 7311.46 Jewelry_Accessories 54633 23.40 49.23 0.00 3600.00 210.44 3600.00 Industrial_Science 30721 25.02 46.47 0.00 2353.03 185.73 2353.03 Baby_Kids 179801 29.02 46.29 0.00 6023.00 159.51 6023.00 Pet_Supplies 13144 22.51 33.02 0.00 887.41 146.7 887.41 Sports_Outdoors 24515 30.11 32.82 0.00 799.95 109.02 799.95 Health_Beauty 17736 18.99 21.85 0.00 399.00 115.07 399.00 Party_Gifts 15546 13.96 9.04 0.00 399.00 64.76 399.00

### Identify products with a rating of 4.0 or higher and a review count in the bottom 30%

In [ ]:
select 
    a.category_type,
    p.*
from amazon_products_ss p
left join amazon_categories_with_type as a on p.category_id = a.id
where p.reviews <= (
    -- number of reviews is 30% cutoff
    select min(reviews)
    from (
        -- setting the 100th percentile
        select reviews,
               ntile(100) over (order by reviews) as percentile
        from amazon_products_ss
        where reviews is not null
    ) t
    where t.percentile <= 30
)
and p.stars >= 4.0 -- 4.0over

category_type asin title imgUrl productURL stars reviews price listPrice category_id isBestSeller boughtInLastMonth Others B09X7BK27V SanDisk 128GB Extreme microSDXC UHS-I Memory Card with Adapter - Up to 190MB/s, C10, U3, V30, 4K, 5K, A2, Micro SD Card - SDSQXAA-128G-GN6MA https://m.media-amazon.com/images/I/71etcRZF-JL._AC_UL320_.jpg https://www.amazon.com/dp/B09X7BK27V 4.8 0 12.99 25.99 76 false 0 Others B00WJDWGA8 HP 63XL Black High-yield Ink Cartridge | Works with HP DeskJet 1112, 2130, 3630 Series; HP ENVY 4510, 4520 Series; HP OfficeJet 3830, 4650, 5200 Series | Eligible for Instant Ink | F6U64AN https://m.media-amazon.com/images/I/71dknWOvquL._AC_UL320_.jpg https://www.amazon.com/dp/B00WJDWGA8 4.7 0 45.89 0.0 76 false 20000 Others B089DM4KDW etguuds 2-Pack 3ft USB C Cable 3A Fast Charge, USB A to Type C Charger Cord Braided Compatible with Samsung Galaxy A10e A20 A50 A51 A71, S20 S10 S9 S8 Plus S10E, Note 20 10 9 8, Moto G7 G8 https://m.media-amazon.com/images/I/61AsLefMRqL._AC_UL320_.jpg https://www.amazon.com/dp/B089DM4KDW 4.6 0 7.99 0.0 76 false 0 Others B07MCYDD62 HP 962 Cyan, Magenta, Yellow Ink Cartridges (3 Count -pack of 1) | Works with HP OfficeJet 9010 Series, HP OfficeJet Pro 9010, 9020 Series | Eligible for Instant Ink | 3YP00AN https://m.media-amazon.com/images/I/71XSbgnGXcS._AC_UL320_.jpg https://www.amazon.com/dp/B07MCYDD62 4.7 0 65.89 0.0 76 false 10000 Others B09X7FXHVJ SanDisk 128GB Extreme PRO SDXC UHS-I Memory Card - C10, U3, V30, 4K UHD, SD Card - SDSDXXD-128G-GN4IN https://m.media-amazon.com/images/I/81wwLOgkLgL._AC_UL320_.jpg https://www.amazon.com/dp/B09X7FXHVJ 4.8 0 22.8 33.49 76 true 0 Others B071YHCML6 HP 64XL Black High-yield Ink Cartridge | Works with HP ENVY Inspire 7950e; ENVY Photo 6200, 7100, 7800; Tango Series | Eligible for Instant Ink | N9J92AN https://m.media-amazon.com/images/I/61XaiQ+8ejL._AC_UL320_.jpg https://www.amazon.com/dp/B071YHCML6 4.7 0 44.45 0.0 76 false 20000 Others B00WR23X5I HP 63 Black Ink Cartridge | Works with HP DeskJet 1112, 2130, 3630 Series; HP ENVY 4510, 4520 Series; HP OfficeJet 3830, 4650, 5200 Series | Eligible for Instant Ink | F6U62AN https://m.media-amazon.com/images/I/71MHmk6IbBL._AC_UL320_.jpg https://www.amazon.com/dp/B00WR23X5I 4.7 0 0.0 0.0 76 false 20000 Others B0BPCZLFS4 Anker USB C Charger Cable [2 Pack, 6ft], 310 Type C Charger Cable Fast Charging, Braided USB A to USB C Cable Fast Charging for Samsung Galaxy Note 10 Note 9/S10+ S10, LG V30 (USB 2.0, Black) https://m.media-amazon.com/images/I/71k0W8zcU2L._AC_UL320_.jpg https://www.amazon.com/dp/B0BPCZLFS4 4.7 0 10.99 0.0 76 false 0 Others B01B6QGJ42 HP 952XL Black High-yield Ink Cartridge | Works with HP OfficeJet 8702, HP OfficeJet Pro 7720, 7740, 8210, 8710, 8720, 8730, 8740 Series | Eligible for Instant Ink | F6U19AN https://m.media-amazon.com/images/I/61cV9q2PBAL._AC_UL320_.jpg https://www.amazon.com/dp/B01B6QGJ42 4.7 0 0.0 0.0 76 false 10000 Others B01BYKD628 HP 902XL Black High-yield Ink Cartridge | Works with HP OfficeJet 6950, 6960 Series, HP OfficeJet Pro 6960, 6970 Series | Eligible for Instant Ink | T6M14AN https://m.media-amazon.com/images/I/71QsmlwPUTL._AC_UL320_.jpg https://www.amazon.com/dp/B01BYKD628 4.6 0 45.89 0.0 76 false 10000 Others B09C5RG6KV Anker USB C Charger, 735 Charger (Nano II 65W), iPad Charger, PPS 3-Port Fast Compact Foldable for MacBook Pro/Air, iPad Pro, Galaxy S23, Dell XPS 13, Note 20/10+, iPhone 15/Pro, Steam Deck, and More https://m.media-amazon.com/images/I/518CnkU772L._AC_UL320_.jpg https://www.amazon.com/dp/B09C5RG6KV 4.7 0 39.99 55.99 76 true 0 Others B07MK5DG9V HP 962XL Black High-yield Ink Cartridge | Works with HP OfficeJet 9010 Series, HP OfficeJet Pro 9010, 9020 Series | Eligible for Instant Ink | 3JA03AN https://m.media-amazon.com/images/I/71YnyARzfPS._AC_UL320_.jpg https://www.amazon.com/dp/B07MK5DG9V 4.7 0 46.89 0.0 76 false 10000 Others B075X7TFY5 Brother Genuine Standard Yield Toner Cartridge, TN730, Replacement Black Toner, Page Yield Up To 1,

### Calculate the percentage of hidden gem products by category
-Hidden Gems: Products with Low Reviews but High Ratings
> Analysis is conducted on products with "lower 30% of reviews and a rating of 4.0 or higher"

In [ ]:
with base as (
	select
		a.*,
		b.category_type
	from (
		select *,
			row_number() over (ORDER BY asin) as asin_seq
		from amazon_products_ss
	) a
	left join amazon_categories_with_type as b on a.category_id = b.id
),

target as (
	select 
		asin_seq
	from base p
	where p.reviews <= (
		-- cutoff 30%
		select min(reviews)
		from (
			select 
				reviews,
				ntile(100) over (order by reviews) as percentile
			from base
			where reviews is not null
		) t
		where t.percentile <= 30
	)
	and p.stars >= 4.0
)

select
	a.category_type,
	count(a.asin_seq) as ea, -- total number of products
	count(case when b.asin_seq is not null then 1 end) as tea -- hidden gem number
from base as a
left join target as b on a.asin_seq = b.asin_seq
group by a.category_type

category_type ea tea Pet_Supplies 13144 9696 Gaming 82611 41743 Others 511846 352822 Crafts_Sewing 42375 28321 Mens_Fashion 141074 93156 Home_Living 56697 44060 Tools_Hardware 18741 17202 Electronics 77070 42727 Travel_Bags 23693 16111 Baby_Kids 179801 93512 Arts_Crafts 29324 14305 Health_Beauty 17736 14954 Toys_Games 44778 29970 Sports_Outdoors 24515 20330 Industrial_Science 30721 4367 Party_Gifts 15546 13742 Automotive 62032 29075 Jewelry_Accessories 54633 28048

### Analyze whether it is a bestseller
* X-axis score (market entry barrier): Normalize < bestseller ratio + total product reviews > 
* Y-axis score (profit potential score): Normalize < total price + average price + average rating > and sum

In [ ]:

with category_base  as (
	select
		category_type,
		total_products,
		bestseller_count,
		(bestseller_count / total_products) as bestseller_ratio, -- number of bestsellers by category
		total_reviews, -- total product reviews
		
		(total_reviews / total_products) as avg_reviews, -- reviews per product
		sum_price, -- total price
		avg_price, -- average price
		avg_stars -- average rating
	from(
		select
			c.category_type,	
			count(*) as total_products, -- otal products by category
			sum(case when p.isBestSeller = true then 1 else 0 end) as bestseller_count, -- number of bestsellers by category
			sum(p.reviews) as total_reviews, -- total product reviews
			
			sum(p.price) as sum_price, -- total price
			avg(p.price) as avg_price, -- average price
			avg(p.stars) as avg_stars -- average rating
		from amazon_products_ss as p
	   left join amazon_categories_with_type as c on p.category_id = c.id
		where p.reviews is not null and p.price is not null and p.stars is not null
		group by c.category_type
	) a
)

, agg_stats as (
-- Overall product averages and standard deviations (for comparing category-specific values)
  select
    avg((bestseller_count * 1.0) / total_products) as avg_bsr,
    stddev_pop((bestseller_count * 1.0) / total_products) as std_bsr,

    avg((total_reviews * 1.0) / total_products) as avg_reviews,
    stddev_pop((total_reviews * 1.0) / total_products) as std_reviews,

    avg(sum_price) as avg_sum_price,
    stddev_pop(sum_price) as std_sum_price,

    avg(avg_stars) as avg_avg_stars,
    stddev_pop(avg_stars) as std_avg_stars
  from category_base
)


select
  a.category_type,
  a.total_products,
  a.bestseller_count,
  round(a.bestseller_ratio, 4) as bestseller_ratio,
  a.total_reviews,
  round(a.avg_reviews, 2) as avg_reviews,
  a.sum_price,
  round(a.avg_price, 2) as avg_price,
  round(a.avg_stars, 2) as avg_stars,

  -- X축 점수
  round(((a.bestseller_ratio - ag.avg_bsr) / ag.std_bsr) +
        ((a.avg_reviews - ag.avg_reviews) / ag.std_reviews), 3) as X_score,

  -- Y축 점수
  round(((a.sum_price - ag.avg_sum_price) / ag.std_sum_price) +
        ((a.avg_stars - ag.avg_avg_stars) / ag.std_avg_stars), 3) as Y_score

from category_base a
cross join agg_stats ag
order by a.category_type

category_type total_products bestseller_count bestseller_ratio total_reviews avg_reviews sum_price avg_price avg_stars X_score Y_score Arts_Crafts 29324 103 0.0035 5893099 200.97 815360.6000000007 27.81 4.16 -0.061 -0.02 Automotive 62032 816 0.0132 17689113 285.16 2790233.289999689 44.98 4.18 1.819 0.433 Baby_Kids 179801 700 0.0039 30971778 172.26 5218124.549999065 29.02 3.89 -0.276 -0.284 Crafts_Sewing 42375 126 0.003 2396161 56.55 785455.9799999594 18.54 3.85 -1.426 -1.324 Electronics 77070 224 0.0029 11446478 148.52 1.1347592830001175E7 147.24 3.82 -0.604 0.639 Gaming 82611 411 0.005 29286649 354.51 2803816.5999996304 33.94 3.76 1.493 -1.29 Health_Beauty 17736 166 0.0094 5192395 292.76 336823.58000001224 18.99 4.31 1.446 0.49 Home_Living 56697 1020 0.018 19694174 347.36 2610657.1599997464 46.05 4.36 2.943 1.167 Industrial_Science 30721 467 0.0152 4169646 135.73 768615.4499999924 25.02 3.51 0.71 -2.733 Jewelry_Accessories 54633 115 0.0021 4103199 75.1 1278212.4399998016 23.4 3.98 -1.36 -0.69 Mens_Fashion 141074 503 0.0036 13389877 94.91 8866895.380002799 62.85 4.04 -1.011 1.073 Others 511846 2652 0.0052 99852469 195.08 2.0196350950022962E7 39.46 4.01 0.08 3.19 Party_Gifts 15546 22 0.0014 55012 3.54 217060.80000000418 13.96 4.29 -2.085 0.402 Pet_Supplies 13144 25 0.0019 0 0.0 295877.97000000067 22.51 3.87 -2.06 -1.346 Sports_Outdoors 24515 898 0.0366 5236880 213.62 738067.2699999588 30.11 4.35 3.905 0.767 Tools_Hardware 18741 179 0.0096 0 0.0 655432.979999993 34.97 4.36 -1.171 0.779 Toys_Games 44778 71 0.0016 7147804 159.63 1191712.6899998747 26.61 4.18 -0.658 0.148 Travel_Bags 23693 22 9.0E-4 1286848 54.31 951652.6399999326 40.17 3.82 -1.684 -1.4

### number of reviews vs. star rating (correlation analysis)

In [ ]:
-- 전체 상품
select
  (
    sum((reviews - stats.avg_reviews) * (stars - stats.avg_stars)) /
    (sqrt(sum(pow(reviews - stats.avg_reviews, 2))) * sqrt(sum(pow(stars - stats.avg_stars, 2))))
  ) as correlation_reviews_stars
from amazon_products_ss, (
  select
    avg(reviews) as avg_reviews,
    avg(stars) as avg_stars
  from amazon_products_ss
  where reviews is not null and stars is not null
) as stats
where reviews is not null and stars is not null;
 


-- 카테고리별
select
  c.category_type,
  count(*) as product_count,
  (
    sum((p.reviews - stats.avg_reviews) * (p.stars - stats.avg_stars)) /
    (sqrt(sum(pow(p.reviews - stats.avg_reviews, 2))) * sqrt(sum(pow(p.stars - stats.avg_stars, 2))))
  ) as correlation_reviews_stars
from amazon_products_ss p
join amazon_categories_with_type c on p.category_id = c.id
join (
  select 
    category_id,
    avg(reviews) as avg_reviews,
    avg(stars) as avg_stars
  from amazon_products_ss
  where reviews > 0 and stars > 0
  group by category_id
) as stats on p.category_id = stats.category_id
where p.reviews is not null and p.stars is not null
group by c.category_type
order by correlation_reviews_stars desc;

category_type product_count correlation_reviews_stars Party_Gifts 8611 0.20575210180679232 Health_Beauty 6080 0.19023107364038883 Crafts_Sewing 10565 0.1325983584456902 Mens_Fashion 81295 0.12936095607008877 Jewelry_Accessories 37628 0.11806835849274229 Electronics 31069 0.11634627942749465 Gaming 48611 0.112292278586745 Travel_Bags 3267 0.10908692684306742 Sports_Outdoors 2291 0.10286524191823618 Toys_Games 9485 0.1016458314159186 Arts_Crafts 14047 0.09049406384303044 Industrial_Science 26288 0.0879084841159089 Baby_Kids 105814 0.08263142900510428 Others 136034 0.07849894231640284 Automotive 34786 0.049241837180622666 Home_Living 14387 0.041606289395737